# Applied Data Science Capstone
## Peer-graded Assignment: Capstone Project - The Battle of Neighborhoods

Now that you have been equipped with the skills and the tools to use location data to explore a geographical location, over the course of two weeks, you will have the opportunity to be as creative as you want and come up with an idea to leverage the Foursquare location data to explore or compare neighborhoods or cities of your choice or to come up with a problem that you can use the Foursquare location data to solve.

### 1) Introduction/Business Problem
Clearly define a problem or an idea of your choice, where you would need to leverage the Foursquare location data to solve or execute. Remember that data science problems always target an audience and are meant to help a group of stakeholders solve a problem, so make sure that you explicitly describe your audience and why they would care about your problem.

The idea of this study is to help people planning to open a new restaurant in Toronto to chose the right location by providing data about the income and population of each neighborhood as well as the competitors already present on the same regions.

### 2) Downloading and Prepping Data
Describe the data that you will be using to solve the problem or execute your idea. Remember that you will need to use the Foursquare location data to solve the problem or execute your idea. You can absolutely use other datasets in combination with the Foursquare location data. So make sure that you provide adequate explanation and discussion, with examples, of the data that you will be using, even if it is only Foursquare location data.

To provide the stakeholders the necessary information I'll be combining Toronto's 2016 Census that contains Population, Average income per Neighborhood with Toronot's Neighborhoods shapefile and Foursquare API to collect competitors on the same neighborhoods.

Toronto's Census data is publicly available at this website: https://www.toronto.ca/city-government/data-research-maps/open-data/open-data-catalogue/#8c732154-5012-9afe-d0cd-ba3ffc813d5a

Toronto Neighborhoods' shapefile is publicly available at this website: https://www.toronto.ca/city-government/data-research-maps/open-data/open-data-catalogue/#a45bd45a-ede8-730e-1abc-93105b2c439f

### 3) Methodology
Methodology section which represents the main component of the report where you discuss and describe any exploratory data analysis that you did, any inferential statistical testing that you performed, and what machine learnings were used and why.

For this report I used a few different maps that could help a new investor to decide the best neighborhood to open a restaurant in Toronto based on it's income, population and available competitors. In order to do that I've used the 2016 Census information combined with choropleth maps to visually display the wealthier and more populational neighborhoods and Foursquare data to display the current restaurants in each region.

### 4) Results
Results section where you discuss the results.

Comparing the maps we can notice the majority of the restaurants grouped on main streets and on the south of the city, although some of the welthiest neighborhoods are up to the north. Also, the areas with a dense population don't reflect on the number of restaurants.

### 5) Discussion
Discussion section where you discuss any observations you noted and any recommendations you can make based on the results.

When I first decided to create this study I was expecting to find clusters of restaurants in certain regions and the final result didn't meet that expectation.

### 6) Conclusion
Conclusion section where you conclude the report.

This report may be helpful for someone planning on opening a restaurant in Toronto, by comparing the current offers and neighborhoods profiles, however it may not cover all variables such as access to public transportation or even the restaurants profiles, so it shall not be used as a single decidion making tool.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library


usage: conda-script.py [-h] [-V] command ...
conda-script.py: error: unrecognized arguments: # uncomment this line if you haven't completed the Foursquare API lab
usage: conda-script.py [-h] [-V] command ...
conda-script.py: error: unrecognized arguments: # uncomment this line if you haven't completed the Foursquare API lab


In [2]:
csv_path='https://www.toronto.ca/ext/open_data/catalog/data_set_files/2016_neighbourhood_profiles.csv'
df = pd.read_csv(csv_path,encoding='latin1')
print('Data loaded')

Data loaded


In [3]:
df.head

<bound method NDFrame.head of                                      Category  \
0                   Neighbourhood Information   
1                   Neighbourhood Information   
2                                  Population   
3                                  Population   
4                                  Population   
5                                  Population   
6                                  Population   
7                                  Population   
8                                  Population   
9                                  Population   
10                                 Population   
11                                 Population   
12                                 Population   
13                                 Population   
14                                 Population   
15                                 Population   
16                                 Population   
17                                 Population   
18                                 Popu

In [4]:
Neighbourhoods = list(df.columns.values)
Neighbourhoods = Neighbourhoods[5:]
print(Neighbourhoods)

['Agincourt North', 'Agincourt South-Malvern West', 'Alderwood', 'Annex', 'Banbury-Don Mills', 'Bathurst Manor', 'Bay Street Corridor', 'Bayview Village', 'Bayview Woods-Steeles', 'Bedford Park-Nortown', 'Beechborough-Greenbrook', 'Bendale', 'Birchcliffe-Cliffside', 'Black Creek', 'Blake-Jones', 'Briar Hill-Belgravia', 'Bridle Path-Sunnybrook-York Mills', 'Broadview North', 'Brookhaven-Amesbury', 'Cabbagetown-South St. James Town', 'Caledonia-Fairbank', 'Casa Loma', 'Centennial Scarborough', 'Church-Yonge Corridor', 'Clairlea-Birchmount', 'Clanton Park', 'Cliffcrest', 'Corso Italia-Davenport', 'Danforth', 'Danforth East York', 'Don Valley Village', 'Dorset Park', 'Dovercourt-Wallace Emerson-Junction', 'Downsview-Roding-CFB', 'Dufferin Grove', 'East End-Danforth', 'Edenbridge-Humber Valley', 'Eglinton East', 'Elms-Old Rexdale', 'Englemount-Lawrence', 'Eringate-Centennial-West Deane', 'Etobicoke West Mall', 'Flemingdon Park', 'Forest Hill North', 'Forest Hill South', 'Glenfield-Jane Heig

In [5]:
dfToronto = pd.DataFrame(index=Neighbourhoods, columns=["Population_2016","Income_2016"])
dfToronto.head()

Population_2016 Income_2016
Agincourt North                          NaN         NaN
Agincourt South-Malvern West             NaN         NaN
Alderwood                                NaN         NaN
Annex                                    NaN         NaN
Banbury-Don Mills                        NaN         NaN

In [6]:
# Population_2016 = Population, 2016
# Income_2016 = Total income: Average amount ($)


for index, row in dfToronto.iterrows():
    dfToronto.at[index, 'Population_2016'] = df[index][2]
    dfToronto.at[index, 'Income_2016'] = df[index][2264]
    

dfToronto.sort_values('Income_2016')

Population_2016 Income_2016
St.Andrew-Windfields                         17,812     100,516
Edenbridge-Humber Valley                     15,535     101,551
Lawrence Park North                          14,607     111,730
Annex                                        30,526     112,766
Yonge-St.Clair                               12,528     114,174
Bedford Park-Nortown                         23,236     123,077
Leaside-Bennington                           16,828     125,564
Kingsway South                                9,271     144,642
Casa Loma                                    10,968     165,047
Lawrence Park South                          15,179     169,203
Forest Hill South                            10,732     204,521
Rosedale-Moore Park                          20,923     207,903
Black Creek                                  21,737      25,989
Mount Olive-Silverstone-Jamestown            32,954      26,548
Oakridge                                     13,845      26,793
Glenfield-Jane Heights                       30,491      27,984
Milliken                                     26,572      28,085
Flemingdon Park                              21,933      28,654
Thorncliffe Park                             21,108      28,875
Humbermede                                   15,545      29,528
Malvern                                      43,794      29,573
York University Heights                      27,593      29,958
Eglinton East                                22,776      30,033
Agincourt North                              29,113      30,414
Taylor-Massey                                15,683      30,430
Humber Summit                                12,416      30,731
Mount Dennis                                 13,593      30,827
Woburn                                       53,485      30,878
Kennedy Park                                 17,123      30,974
Bridle Path-Sunnybrook-York Mills             9,266     308,010
Ionview                                      13,641      31,383
Dorset Park                                  25,003      31,692
West Humber-Clairville                       33,312      31,771
Steeles                                      24,623      31,786
Rustic                                        9,941      31,800
Agincourt South-Malvern West                 23,757      31,825
L'Amoreaux                                   43,993      31,826
Elms-Old Rexdale                              9,456      32,012
Morningside                                  17,455      32,291
Brookhaven-Amesbury                          17,757      32,483
North St. James Town                         18,615      32,648
Westminster-Branson                          26,274      32,724
Thistletown-Beaumond Heights                 10,360      32,815
Scarborough Village                          16,724      32,913
Weston                                       17,992      32,997
Bendale                                      29,960      33,256
Keelesdale-Eglinton West                     11,058      33,316
West Hill                                    27,392      33,323
Weston-Pelham Park                           11,098      33,528
Beechborough-Greenbrook                       6,577      33,829
Rockcliffe-Smythe                            22,246      34,059
Downsview-Roding-CFB                         35,052      34,168
Tam O'Shanter-Sullivan                       27,446      34,200
Rexdale-Kipling                              10,529      34,418
Regent Park                                  10,803      34,597
Briar Hill-Belgravia                         14,257      34,768
Newtonbrook West                             23,831      34,904
Wexford/Maryvale                             27,917      35,047
Caledonia-Fairbank                            9,955      35,112
South Parkdale                               21,849      35,207
Victoria Village                             17,510      35,786
Clairlea-Birchmount                          26,984      36,232
Plea